In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [3]:
# Convolutional neural network (two convolutional layers)
class RNN_AT(nn.Module):
    def __init__(self, num_classes=4):
        super(RNN_AT, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64)
        self.rnn = nn.RNN(64,256,dropout=0.25,bidirectional=True)
        self.fc1 = nn.Linear(512, 64)
        self.fc2 = nn.Linear(64, num_classes)
        #attention parameter
        self.u = torch.randn(8,device=device,requires_grad=True)
        self.fc_attention = nn.Linear(512, 8)
        self.ac_attention = nn.Softmax(dim=1)
        
    def forward(self, x):    
       
        #b,64,64
        x, _= self.rnn(x)
        #b,64,512
        temp1 = self.fc_attention(x)
        temp1 = F.tanh(temp1)
        #b,64,8
        alpha = torch.tensordot(temp1,self.u,1)
        alpha = self.ac_attention(alpha)
        #b,64 = b,64,8 .* 8
        alpha = alpha.reshape(-1,64,1)
        #b,64,1
        x = torch.mul(x,alpha)
        #b,64,512 * b,64,1 = b,64,512
        x = torch.sum(x,dim=1)
        #b,64,512 -> b,512
        x = self.fc1(x)
        x = self.bn1(x)
        x = F.softplus(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [4]:
test = RNN_AT(4).to(device)
a = torch.randn(10,64,64)
a = a.to(device)
out = test(a)
out.shape

C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\modules\rnn.py:62: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.25 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\functional.py:1795: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")


torch.Size([10, 4])

In [5]:
writer = SummaryWriter()

In [6]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [7]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [8]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [9]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [10]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [11]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [12]:
model = RNN_AT(num_classes).to(device)

In [13]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [14]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 32.8125%, Training Loss: 1.5210%
Epoch [1/300], Step [2/225], Training Accuracy: 32.0312%, Training Loss: 1.5378%
Epoch [1/300], Step [3/225], Training Accuracy: 32.2917%, Training Loss: 1.5334%
Epoch [1/300], Step [4/225], Training Accuracy: 31.6406%, Training Loss: 1.5112%
Epoch [1/300], Step [5/225], Training Accuracy: 31.5625%, Training Loss: 1.4916%
Epoch [1/300], Step [6/225], Training Accuracy: 29.9479%, Training Loss: 1.4918%
Epoch [1/300], Step [7/225], Training Accuracy: 29.6875%, Training Loss: 1.4957%
Epoch [1/300], Step [8/225], Training Accuracy: 28.7109%, Training Loss: 1.5008%
Epoch [1/300], Step [9/225], Training Accuracy: 28.1250%, Training Loss: 1.5201%
Epoch [1/300], Step [10/225], Training Accuracy: 27.9688%, Training Loss: 1.5156%
Epoch [1/300], Step [11/225], Training Accuracy: 27.5568%, Training Loss: 1.5176%
Epoch [1/300], Step [12/225], Training Accuracy: 27.3438%, Training Loss: 1.5159%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [119/225], Training Accuracy: 30.2127%, Training Loss: 1.3945%
Epoch [1/300], Step [120/225], Training Accuracy: 30.1693%, Training Loss: 1.3949%
Epoch [1/300], Step [121/225], Training Accuracy: 30.1782%, Training Loss: 1.3947%
Epoch [1/300], Step [122/225], Training Accuracy: 30.0845%, Training Loss: 1.3954%
Epoch [1/300], Step [123/225], Training Accuracy: 30.0686%, Training Loss: 1.3955%
Epoch [1/300], Step [124/225], Training Accuracy: 30.1159%, Training Loss: 1.3954%
Epoch [1/300], Step [125/225], Training Accuracy: 30.1250%, Training Loss: 1.3959%
Epoch [1/300], Step [126/225], Training Accuracy: 30.1463%, Training Loss: 1.3956%
Epoch [1/300], Step [127/225], Training Accuracy: 30.1673%, Training Loss: 1.3956%
Epoch [1/300], Step [128/225], Training Accuracy: 30.1514%, Training Loss: 1.3953%
Epoch [1/300], Step [129/225], Training Accuracy: 30.2326%, Training Loss: 1.3945%
Epoch [1/300], Step [130/225], Training Accuracy: 30.2043%, Training Loss: 1.3943%
Epoc

Epoch [2/300], Step [2/225], Training Accuracy: 36.7188%, Training Loss: 1.2927%
Epoch [2/300], Step [3/225], Training Accuracy: 32.8125%, Training Loss: 1.3180%
Epoch [2/300], Step [4/225], Training Accuracy: 32.4219%, Training Loss: 1.3151%
Epoch [2/300], Step [5/225], Training Accuracy: 34.3750%, Training Loss: 1.3145%
Epoch [2/300], Step [6/225], Training Accuracy: 34.3750%, Training Loss: 1.3107%
Epoch [2/300], Step [7/225], Training Accuracy: 35.0446%, Training Loss: 1.3089%
Epoch [2/300], Step [8/225], Training Accuracy: 35.1562%, Training Loss: 1.3060%
Epoch [2/300], Step [9/225], Training Accuracy: 34.2014%, Training Loss: 1.3159%
Epoch [2/300], Step [10/225], Training Accuracy: 34.3750%, Training Loss: 1.3107%
Epoch [2/300], Step [11/225], Training Accuracy: 34.0909%, Training Loss: 1.3158%
Epoch [2/300], Step [12/225], Training Accuracy: 33.3333%, Training Loss: 1.3169%
Epoch [2/300], Step [13/225], Training Accuracy: 34.1346%, Training Loss: 1.3148%
Epoch [2/300], Step [14/

Epoch [2/300], Step [112/225], Training Accuracy: 35.4492%, Training Loss: 1.3065%
Epoch [2/300], Step [113/225], Training Accuracy: 35.3429%, Training Loss: 1.3076%
Epoch [2/300], Step [114/225], Training Accuracy: 35.4167%, Training Loss: 1.3068%
Epoch [2/300], Step [115/225], Training Accuracy: 35.4755%, Training Loss: 1.3072%
Epoch [2/300], Step [116/225], Training Accuracy: 35.4930%, Training Loss: 1.3068%
Epoch [2/300], Step [117/225], Training Accuracy: 35.4033%, Training Loss: 1.3078%
Epoch [2/300], Step [118/225], Training Accuracy: 35.4476%, Training Loss: 1.3077%
Epoch [2/300], Step [119/225], Training Accuracy: 35.3598%, Training Loss: 1.3078%
Epoch [2/300], Step [120/225], Training Accuracy: 35.4036%, Training Loss: 1.3081%
Epoch [2/300], Step [121/225], Training Accuracy: 35.4081%, Training Loss: 1.3083%
Epoch [2/300], Step [122/225], Training Accuracy: 35.4252%, Training Loss: 1.3082%
Epoch [2/300], Step [123/225], Training Accuracy: 35.3913%, Training Loss: 1.3081%
Epoc

Epoch [2/300], Step [223/225], Training Accuracy: 36.0146%, Training Loss: 1.2997%
Epoch [2/300], Step [224/225], Training Accuracy: 36.0212%, Training Loss: 1.2994%
Epoch [2/300], Step [225/225], Training Accuracy: 35.9992%, Training Loss: 1.2996%
Epoch [3/300], Step [1/225], Training Accuracy: 42.1875%, Training Loss: 1.2115%
Epoch [3/300], Step [2/225], Training Accuracy: 37.5000%, Training Loss: 1.2971%
Epoch [3/300], Step [3/225], Training Accuracy: 37.5000%, Training Loss: 1.3084%
Epoch [3/300], Step [4/225], Training Accuracy: 37.5000%, Training Loss: 1.3007%
Epoch [3/300], Step [5/225], Training Accuracy: 37.1875%, Training Loss: 1.2999%
Epoch [3/300], Step [6/225], Training Accuracy: 37.5000%, Training Loss: 1.3072%
Epoch [3/300], Step [7/225], Training Accuracy: 36.8304%, Training Loss: 1.3062%
Epoch [3/300], Step [8/225], Training Accuracy: 36.3281%, Training Loss: 1.2981%
Epoch [3/300], Step [9/225], Training Accuracy: 36.2847%, Training Loss: 1.2992%
Epoch [3/300], Step [1

...

Epoch [298/300], Step [157/225], Training Accuracy: 99.6417%, Training Loss: 0.0179%
Epoch [298/300], Step [158/225], Training Accuracy: 99.6440%, Training Loss: 0.0178%
Epoch [298/300], Step [159/225], Training Accuracy: 99.6462%, Training Loss: 0.0178%
Epoch [298/300], Step [160/225], Training Accuracy: 99.6484%, Training Loss: 0.0178%
Epoch [298/300], Step [161/225], Training Accuracy: 99.6506%, Training Loss: 0.0178%
Epoch [298/300], Step [162/225], Training Accuracy: 99.6528%, Training Loss: 0.0177%
Epoch [298/300], Step [163/225], Training Accuracy: 99.6549%, Training Loss: 0.0177%
Epoch [298/300], Step [164/225], Training Accuracy: 99.6570%, Training Loss: 0.0176%
Epoch [298/300], Step [165/225], Training Accuracy: 99.6591%, Training Loss: 0.0175%
Epoch [298/300], Step [166/225], Training Accuracy: 99.6611%, Training Loss: 0.0175%
Epoch [298/300], Step [167/225], Training Accuracy: 99.6632%, Training Loss: 0.0175%
Epoch [298/300], Step [168/225], Training Accuracy: 99.6652%, Tra

Epoch [299/300], Step [36/225], Training Accuracy: 99.7396%, Training Loss: 0.0151%
Epoch [299/300], Step [37/225], Training Accuracy: 99.7466%, Training Loss: 0.0151%
Epoch [299/300], Step [38/225], Training Accuracy: 99.7122%, Training Loss: 0.0154%
Epoch [299/300], Step [39/225], Training Accuracy: 99.7196%, Training Loss: 0.0155%
Epoch [299/300], Step [40/225], Training Accuracy: 99.7266%, Training Loss: 0.0155%
Epoch [299/300], Step [41/225], Training Accuracy: 99.7332%, Training Loss: 0.0153%
Epoch [299/300], Step [42/225], Training Accuracy: 99.7024%, Training Loss: 0.0160%
Epoch [299/300], Step [43/225], Training Accuracy: 99.7093%, Training Loss: 0.0158%
Epoch [299/300], Step [44/225], Training Accuracy: 99.6804%, Training Loss: 0.0161%
Epoch [299/300], Step [45/225], Training Accuracy: 99.6875%, Training Loss: 0.0158%
Epoch [299/300], Step [46/225], Training Accuracy: 99.6943%, Training Loss: 0.0156%
Epoch [299/300], Step [47/225], Training Accuracy: 99.7008%, Training Loss: 

Epoch [299/300], Step [145/225], Training Accuracy: 99.6875%, Training Loss: 0.0166%
Epoch [299/300], Step [146/225], Training Accuracy: 99.6896%, Training Loss: 0.0165%
Epoch [299/300], Step [147/225], Training Accuracy: 99.6918%, Training Loss: 0.0165%
Epoch [299/300], Step [148/225], Training Accuracy: 99.6938%, Training Loss: 0.0164%
Epoch [299/300], Step [149/225], Training Accuracy: 99.6959%, Training Loss: 0.0164%
Epoch [299/300], Step [150/225], Training Accuracy: 99.6979%, Training Loss: 0.0163%
Epoch [299/300], Step [151/225], Training Accuracy: 99.6999%, Training Loss: 0.0163%
Epoch [299/300], Step [152/225], Training Accuracy: 99.7019%, Training Loss: 0.0163%
Epoch [299/300], Step [153/225], Training Accuracy: 99.7038%, Training Loss: 0.0163%
Epoch [299/300], Step [154/225], Training Accuracy: 99.7058%, Training Loss: 0.0162%
Epoch [299/300], Step [155/225], Training Accuracy: 99.6976%, Training Loss: 0.0164%
Epoch [299/300], Step [156/225], Training Accuracy: 99.6995%, Tra

Epoch [300/300], Step [28/225], Training Accuracy: 99.6652%, Training Loss: 0.0179%
Epoch [300/300], Step [29/225], Training Accuracy: 99.6767%, Training Loss: 0.0176%
Epoch [300/300], Step [30/225], Training Accuracy: 99.6875%, Training Loss: 0.0174%
Epoch [300/300], Step [31/225], Training Accuracy: 99.6976%, Training Loss: 0.0174%
Epoch [300/300], Step [32/225], Training Accuracy: 99.6582%, Training Loss: 0.0174%
Epoch [300/300], Step [33/225], Training Accuracy: 99.6686%, Training Loss: 0.0176%
Epoch [300/300], Step [34/225], Training Accuracy: 99.6783%, Training Loss: 0.0179%
Epoch [300/300], Step [35/225], Training Accuracy: 99.6429%, Training Loss: 0.0182%
Epoch [300/300], Step [36/225], Training Accuracy: 99.6528%, Training Loss: 0.0178%
Epoch [300/300], Step [37/225], Training Accuracy: 99.6199%, Training Loss: 0.0182%
Epoch [300/300], Step [38/225], Training Accuracy: 99.6299%, Training Loss: 0.0181%
Epoch [300/300], Step [39/225], Training Accuracy: 99.6394%, Training Loss: 

Epoch [300/300], Step [133/225], Training Accuracy: 99.6828%, Training Loss: 0.0173%
Epoch [300/300], Step [134/225], Training Accuracy: 99.6735%, Training Loss: 0.0174%
Epoch [300/300], Step [135/225], Training Accuracy: 99.6759%, Training Loss: 0.0174%
Epoch [300/300], Step [136/225], Training Accuracy: 99.6783%, Training Loss: 0.0173%
Epoch [300/300], Step [137/225], Training Accuracy: 99.6807%, Training Loss: 0.0172%
Epoch [300/300], Step [138/225], Training Accuracy: 99.6716%, Training Loss: 0.0175%
Epoch [300/300], Step [139/225], Training Accuracy: 99.6740%, Training Loss: 0.0175%
Epoch [300/300], Step [140/225], Training Accuracy: 99.6763%, Training Loss: 0.0176%
Epoch [300/300], Step [141/225], Training Accuracy: 99.6786%, Training Loss: 0.0175%
Epoch [300/300], Step [142/225], Training Accuracy: 99.6809%, Training Loss: 0.0175%
Epoch [300/300], Step [143/225], Training Accuracy: 99.6831%, Training Loss: 0.0175%
Epoch [300/300], Step [144/225], Training Accuracy: 99.6853%, Tra

In [15]:
from playsound import playsound
playsound(u"sound.mp3")

In [16]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 41.07837687604225 %
